In [1]:
import pandas as pd
from cobra import io
from cobra.core import Metabolite, Reaction

import logging
logging.basicConfig()
logger = logging.getLogger('logger')

cobra/__init__.py:33 FutureWarning: Python 2 is reaching end of life (see https://www.python.org/dev/peps/pep-0373/) and many cobra dependencies have already dropped support. At the moment it *should* still work but we will no longer actively maintain Python 2 support.


## Add gene association

In [2]:



#model = io.sbml.read_sbml_model("/home/sanu/Downloads/core_model_4GA_20_10_17.xml",use_fbc_package=False)
fname = "/home/sanu/Documents/Scripts/git/plantcoremetabolism-model/PlantCoreMetabolism_v2_0_0.xml"
model = io.sbml.read_sbml_model(fname,use_fbc_package=True)

In [3]:
#change Biomass_tx to Protein_biomass
rxn = model.reactions.get_by_id("Biomass_tx")
rxn.id = "Protein_biomass_tx"
for met in ["K_b","Ca_b","Mg_b"]:
    met  = model.metabolites.get_by_id(met)
    coeff = rxn.metabolites.get(met)
    rxn.add_metabolites({met:-1*coeff})
met = Metabolite("Protein_b",name="Protein_biomass",compartment="b")
formula_dict = rxn.check_mass_balance()
met.formula = "".join([atom+str(formula_dict[atom]*-1) for atom in formula_dict.keys() if atom != "charge"])
#met.charge = formula_dict["charge"]*-1
rxn.add_metabolites({met:1})

In [4]:
import pythoncyc
from Functions import *

soy = pythoncyc.select_organism("soy")

In [5]:
model = addGPR2Models(model,soy)

--------------
This list of metabolic reactions are ignored
['RXN_9650_p', '2_KETO_ADIPATE_DEHYDROG_RXN_m', 'Phytol_biosynthesis_p', 'CYSTEINE_AMINOTRANSFERASE_RXN_m', 'GLYCINE_TRNA_LIGASE_RXN_c', 'RXN66_1_c', 'RXN_9648_p', 'RXN-9651', 'Plastidial_ATP_Synthase_p', 'GGPP_biosynthesis_p', 'RXN_9653_p', 'lycopene_biosynthesis_p', 'RXN_2141_p', 'SUCCINYL_COA_HYDROLASE_RXN_m', 'PROTON_ATPase_c', 'MDA_Fd_Ascorbate_p', 'MercaptoPyruvateSulfurtransferase_m', 'Phytol_degradation_p', 'RXN_9652_p', 'A_B_oxidation_x', 'unlProtHYPO_c', 'Mitochondrial_ATP_Synthase_m', 'IPP_biosynthesis_c', 'Mehler_Reaction_p', 'Beta_Oxidation_x', 'HMBPP_synthesis_p', 'OROTATE_REDUCTASE_NADH_RXN_p', 'Ferredoxin_Plastoquinone_Reductase_p', 'RXN_9651_p', 'NADPH_Dehydrogenase_p', 'Plastoquinol_Oxidase_p', 'SUCCINATE_COA_LIGASE_GDP_FORMING_RXN_m', 'RXN_1781_v', 'PREPHENATE_DEHYDROGENASE_NADP_RXN_p', 'PREPHENATEDEHYDROG_RXN_p', 'MALEYLACETOACETATE_ISOMERASE_RXN_c', 'RXN_9654_p', 'LCYSDESULF_RXN_c', 'RXN_9958_NAD_m', 'HEXO

#### Generate a core model

In [6]:
io.write_sbml_model(model,"/home/sanu/Documents/Scripts/git/tissue-specific-FBA-models/Data/Soy_core_model_GA.sbml")

In [7]:
import pandas as pd

df1 = pd.read_csv("/home/sanu/Downloads/cropPAL2_localisations_20171025.csv")
df3 = pd.read_csv("/home/sanu/Downloads/cropPAL2_main_predictors_20171025_mod.csv",sep=",")
df2 = pd.read_csv("/home/sanu/Downloads/Glyma_Correspondence_Report_2020012271906.csv",sep="\t")
df2["Wm82.a2.v1"] = df2["Wm82.a2.v1"].transform(lambda x:x.replace(" ",""))
df4 = pd.read_csv("/home/sanu/Downloads/Glyma_Correspondence_Report_2020013054330.csv",sep="\t")

/home/sanu/.local/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2714 DtypeWarning: Columns (2,12,13,14,15,16,17,19,20,22,23,24) have mixed types. Specify dtype option on import or set low_memory=False.


In [8]:
for gene in model.genes:
    geneParts = gene.id.split(".")
    tempDf2 = df4[df4["Submitted Feature"]==geneParts[0]+"."+geneParts[1].lower()]
    #print tempDf2
    if tempDf2["Wm82.a1.v1.1"].to_string(index=False)=="no correspondence":
        continue
    else:
        GID = tempDf2["Wm82.a1.v1.1"].str.upper().to_string(index=False)
        
        print gene.id
        print GID
        
        default = {"cytosol":0,"mitochondrion":0,"plastid":0,"peroxisome":0,"vacuole":0, "golgi":0,
                   "nucleus":0,"endoplasmic reticulum":0,"extracellular":0,"plasma membrane":0,
                   "cytoskeleton":0,"unclear":0}
        
        experiment = default.copy()
        tempDf3 = df1[df1["locus"].str.contains(GID)]
        for loc in tempDf3["location"]:
            experiment[loc]=experiment[loc]+1
            
        prediction = default.copy()
        tempDf4 = df3[df3["locus"].str.contains(GID)]
        for cols in tempDf4.columns:
            if ("location") in cols and (cols != "location_all_predictors" and cols!="location_consensus"):
                for loc in tempDf4[cols]:
                    if "," in str(loc):
                        for loc2 in loc.split(","):
                            if str(loc2)=="nan":
                                continue
                            prediction[loc2]=prediction[loc2]+1
                    else:
                        if str(loc)=="nan":
                            continue
                        prediction[loc]=prediction[loc]+1
        
        
        if sum(experiment.values())==0 and sum(prediction.values())==0:
            continue
        consensus = experiment.copy()
        for loc in prediction.keys():
                consensus[loc]=consensus[loc]+(float(prediction[loc])/sum(prediction.values()))
        print tempDf4
        print "---experimental---"
        print experiment
        print "---prediction---"
        print prediction
        print "---consensus---"
        print consensus
        gene.notes["cropPal2_localization"]=consensus
        

Glyma.19G017200
GLYMA19G02031
                  locus  taxaid assembly  \
167932  GLYMA19G02031.1    3847       19   

                                              description  ests  flcdnas  \
167932  gene_biotype:protein_coding transcript_biotype...     0        0   

        residues      mwt       pi     gravy    ...     location_plantmploc  \
167932       568  62762.8  5.47757 -0.118134    ...                 cytosol   

       location_pprowler location_predotar location_targetp  \
167932     mitochondrion               NaN              NaN   

       location_wolfpsort location_yloc location_epiloc location_pts1  \
167932            cytosol       cytosol         plastid           NaN   

          athaliana   blast_id  
167932  AT5G42740.1  3872771.0  

[1 rows x 26 columns]
---experimental---
{'unclear': 0, 'cytosol': 0, 'endoplasmic reticulum': 0, 'golgi': 0, 'vacuole': 0, 'plastid': 0, 'nucleus': 0, 'peroxisome': 0, 'mitochondrion': 0, 'cytoskeleton': 0, 'extracellular': 0, 

                  locus  taxaid assembly  \
155160  GLYMA04G09800.1    3847        4   
155161  GLYMA04G09800.2    3847        4   

                                              description  ests  flcdnas  \
155160  gene_biotype:protein_coding transcript_biotype...     0        0   
155161  gene_biotype:protein_coding transcript_biotype...     0        0   

        residues      mwt       pi     gravy    ...    location_plantmploc  \
155160       648  71106.4  6.12281 -0.095525    ...                cytosol   
155161       615  67356.8  5.72722 -0.140488    ...                cytosol   

       location_pprowler location_predotar location_targetp  \
155160           plastid           plastid          plastid   
155161           plastid           plastid          plastid   

       location_wolfpsort location_yloc location_epiloc location_pts1  \
155160            plastid       cytosol         nucleus           NaN   
155161            plastid       cytosol         nucleus           N

                  locus  taxaid assembly  \
152933  GLYMA05G01300.1    3847        5   
152934  GLYMA05G01300.2    3847        5   
152935  GLYMA05G01300.4    3847        5   
152936  GLYMA05G01300.3    3847        5   
152937  GLYMA05G01300.5    3847        5   
152938  GLYMA05G01300.6    3847        5   

                                              description  ests  flcdnas  \
152933  gene_biotype:protein_coding transcript_biotype...     0        0   
152934  gene_biotype:protein_coding transcript_biotype...     0        0   
152935  gene_biotype:protein_coding transcript_biotype...     0        0   
152936  gene_biotype:protein_coding transcript_biotype...     0        0   
152937  gene_biotype:protein_coding transcript_biotype...     0        0   
152938  gene_biotype:protein_coding transcript_biotype...     0        0   

        residues      mwt       pi     gravy    ...    location_plantmploc  \
152933       554  61442.0  7.59121 -0.141877    ...          mitochondrion   
15

                  locus  taxaid assembly  \
165603  GLYMA01G33761.1    3847        1   

                                              description  ests  flcdnas  \
165603  gene_biotype:protein_coding transcript_biotype...     0        0   

        residues      mwt       pi     gravy    ...    location_plantmploc  \
165603       338  36826.3  6.35476 -0.123077    ...                plastid   

       location_pprowler location_predotar location_targetp  \
165603     mitochondrion     mitochondrion    mitochondrion   

       location_wolfpsort  location_yloc location_epiloc location_pts1  \
165603            plastid  mitochondrion         plastid           NaN   

          athaliana  blast_id  
165603  AT4G08900.1  104338.0  

[1 rows x 26 columns]
---experimental---
{'unclear': 0, 'cytosol': 0, 'endoplasmic reticulum': 0, 'golgi': 0, 'vacuole': 0, 'plastid': 0, 'nucleus': 0, 'peroxisome': 0, 'mitochondrion': 1, 'cytoskeleton': 0, 'extracellular': 0, 'plasma membrane': 0}
---predict

                  locus  taxaid assembly  \
110005  GLYMA16G08285.1    3847       16   

                                              description  ests  flcdnas  \
110005  gene_biotype:protein_coding transcript_biotype...     0        0   

        residues      mwt       pi    gravy    ...     location_plantmploc  \
110005        99  11181.6  4.75754  0.19596    ...           mitochondrion   

                                        location_pprowler location_predotar  \
110005  endoplasmic reticulum,extracellular,golgi,plas...               NaN   

                                         location_targetp location_wolfpsort  \
110005  endoplasmic reticulum,extracellular,golgi,plas...            cytosol   

       location_yloc location_epiloc location_pts1    athaliana   blast_id  
110005       cytosol         nucleus           NaN  AT4G22930.1  3326904.0  

[1 rows x 26 columns]
---experimental---
{'unclear': 0, 'cytosol': 0, 'endoplasmic reticulum': 0, 'golgi': 0, 'vacuole': 0, 'p

...

                  locus  taxaid assembly  \
109982  GLYMA16G08460.1    3847       16   
109983  GLYMA16G08460.2    3847       16   

                                              description  ests  flcdnas  \
109982  gene_biotype:protein_coding transcript_biotype...     0        0   
109983  gene_biotype:protein_coding transcript_biotype...     0        0   

        residues      mwt       pi     gravy    ...     location_plantmploc  \
109982       591  65198.4  5.89042 -0.138240    ...                 plastid   
109983       531  58631.4  5.39201 -0.128249    ...                 plastid   

       location_pprowler location_predotar location_targetp  \
109982     mitochondrion               NaN              NaN   
109983     mitochondrion               NaN              NaN   

       location_wolfpsort location_yloc location_epiloc location_pts1  \
109982            plastid       cytosol         plastid           NaN   
109983            plastid       cytosol         plastid         

                 locus  taxaid      assembly  \
167311  GLYMA0175S50.1    3847  scaffold_175   

                                              description  ests  flcdnas  \
167311  gene_biotype:protein_coding transcript_biotype...     0        0   

        residues      mwt       pi    gravy   ...    location_plantmploc  \
167311       111  12109.7  7.77473  0.11982   ...                plastid   

                                        location_pprowler location_predotar  \
167311  endoplasmic reticulum,extracellular,golgi,plas...               NaN   

       location_targetp location_wolfpsort location_yloc location_epiloc  \
167311              NaN            plastid       cytosol         plastid   

       location_pts1    athaliana blast_id  
167311           NaN  AT1G79750.1   6080.0  

[1 rows x 26 columns]
---experimental---
{'unclear': 0, 'cytosol': 0, 'endoplasmic reticulum': 0, 'golgi': 0, 'vacuole': 0, 'plastid': 0, 'nucleus': 0, 'peroxisome': 0, 'mitochondrion': 0, 'cyto

                  locus  taxaid assembly  \
171608  GLYMA20G07060.1    3847       20   

                                              description  ests  flcdnas  \
171608  gene_biotype:protein_coding transcript_biotype...     0        0   

        residues      mwt       pi     gravy    ...     location_plantmploc  \
171608       674  74321.4  6.97235 -0.092285    ...              peroxisome   

       location_pprowler location_predotar location_targetp  \
171608     mitochondrion               NaN              NaN   

       location_wolfpsort location_yloc location_epiloc location_pts1  \
171608            plastid    peroxisome         cytosol           NaN   

          athaliana   blast_id  
171608  AT2G04350.1  4086986.0  

[1 rows x 26 columns]
---experimental---
{'unclear': 0, 'cytosol': 0, 'endoplasmic reticulum': 1, 'golgi': 0, 'vacuole': 0, 'plastid': 0, 'nucleus': 0, 'peroxisome': 0, 'mitochondrion': 0, 'cytoskeleton': 0, 'extracellular': 0, 'plasma membrane': 0}
---predi

                  locus  taxaid assembly  \
171171  GLYMA20G01060.1    3847       20   

                                              description  ests  flcdnas  \
171171  gene_biotype:protein_coding transcript_biotype...     0        0   

        residues      mwt       pi    gravy    ...     location_plantmploc  \
171171       660  73835.7  6.81362 -0.20803    ...              peroxisome   

       location_pprowler location_predotar location_targetp  \
171171     mitochondrion               NaN              NaN   

       location_wolfpsort location_yloc location_epiloc location_pts1  \
171171            nucleus    peroxisome             NaN           NaN   

          athaliana   blast_id  
171171  AT1G49430.1  4063648.0  

[1 rows x 26 columns]
---experimental---
{'unclear': 0, 'cytosol': 0, 'endoplasmic reticulum': 0, 'golgi': 0, 'vacuole': 0, 'plastid': 0, 'nucleus': 0, 'peroxisome': 0, 'mitochondrion': 0, 'cytoskeleton': 0, 'extracellular': 0, 'plasma membrane': 0}
---predict

                  locus  taxaid assembly  \
164043  GLYMA02G01370.3    3847        2   
164044  GLYMA02G01370.4    3847        2   
164045  GLYMA02G01370.5    3847        2   

                                              description  ests  flcdnas  \
164043  gene_biotype:protein_coding transcript_biotype...     0        0   
164044  gene_biotype:protein_coding transcript_biotype...     0        0   
164045  gene_biotype:protein_coding transcript_biotype...     0        0   

        residues      mwt       pi     gravy    ...    location_plantmploc  \
164043       660  74386.2  6.96095 -0.214545    ...             peroxisome   
164044       660  74386.2  6.96095 -0.214545    ...             peroxisome   
164045       660  74386.2  6.96095 -0.214545    ...             peroxisome   

       location_pprowler location_predotar location_targetp  \
164043     mitochondrion               NaN              NaN   
164044     mitochondrion               NaN              NaN   
164045     mitoc

In [9]:
def gene_localization(gene):
    locDict={'cytoskeleton': "",'cytosol': "c",'endoplasmic reticulum': "r",'extracellular': "e",
             'golgi': "g",'mitochondrion': "m",'nucleus': "n",'peroxisome': "x",'plasma membrane': "ec",
             'plastid': "p",'vacuole': "v"}
    majorLoc = set()
    for loc in gene.notes["cropPal2_localization"].keys():
        if gene.notes["cropPal2_localization"][loc] == max(gene.notes["cropPal2_localization"].values()):
            majorLoc.add(locDict[loc])
    return majorLoc

In [26]:
removeGeneDict = dict()
model2 = model.copy()
for rxn in model2.reactions:
    removeGeneDict[rxn.id]=list()
    if len(rxn.genes)>0:
        compSet = set()
        for met in rxn.metabolites.keys():
            compSet.add(met.compartment)
        for gene in rxn.genes:
            if "cropPal2_localization" in gene.notes.keys():
                print rxn.id
                print compSet
                print gene.id
                geneCompSet = gene_localization(gene)
                print geneCompSet
                print "---------"
                if len(geneCompSet.intersection(compSet))==0:
                    removeGeneDict[rxn.id].append(gene)

ACETYLGLUTKIN_RXN_p
set(['p'])
Glyma.04G073800
set(['p'])
---------
ACETYLGLUTKIN_RXN_p
set(['p'])
Glyma.06G074900
set(['p'])
---------
DIAMINOPIMDECARB_RXN_p
set(['p'])
Glyma.10G053600
set(['p'])
---------
DIAMINOPIMDECARB_RXN_p
set(['p'])
Glyma.03G181200
set(['n'])
---------
DIAMINOPIMDECARB_RXN_p
set(['p'])
Glyma.13G140700
set(['p'])
---------
DIAMINOPIMDECARB_RXN_p
set(['p'])
Glyma.19G182000
set(['p', 'n'])
---------
F16ALDOLASE_RXN_p
set(['p'])
Glyma.12G037400
set(['p'])
---------
F16ALDOLASE_RXN_p
set(['p'])
Glyma.10G066700
set(['m'])
---------
F16ALDOLASE_RXN_p
set(['p'])
Glyma.10G268500
set(['r'])
---------
F16ALDOLASE_RXN_p
set(['p'])
Glyma.14G189400
set(['n'])
---------
F16ALDOLASE_RXN_p
set(['p'])
Glyma.20G122500
set(['n'])
---------
F16ALDOLASE_RXN_p
set(['p'])
Glyma.12G153000
set(['p'])
---------
F16ALDOLASE_RXN_p
set(['p'])
Glyma.13G151800
set(['m'])
---------
F16ALDOLASE_RXN_p
set(['p'])
Glyma.11G111100
set(['p'])
---------
F16ALDOLASE_RXN_p
set(['p'])
Glyma.03G191500
se

set(['p'])
Glyma.05G129600
set(['p', 'r', 'n'])
---------
RXN_9516_p
set(['p'])
Glyma.08G084300
set(['p', 'n'])
---------
RXN_9516_p
set(['p'])
Glyma.18G270400
set(['m'])
---------
F16BDEPHOS_RXN_p
set(['p'])
Glyma.08G182300
set(['c'])
---------
F16BDEPHOS_RXN_p
set(['p'])
Glyma.20G166400
set(['c'])
---------
F16BDEPHOS_RXN_p
set(['p'])
Glyma.08G067500
set(['p'])
---------
F16BDEPHOS_RXN_p
set(['p'])
Glyma.16G168000
set(['n'])
---------
F16BDEPHOS_RXN_p
set(['p'])
Glyma.07G182300
set(['p'])
---------
F16BDEPHOS_RXN_p
set(['p'])
Glyma.15G050100
set(['c'])
---------
F16BDEPHOS_RXN_p
set(['p'])
Glyma.07G142700
set(['p', 'n'])
---------
F16BDEPHOS_RXN_p
set(['p'])
Glyma.18G193600
set(['p', 'n'])
---------
F16BDEPHOS_RXN_p
set(['p'])
Glyma.10G225400
set(['c'])
---------
1_PERIOD_2_PERIOD_1_PERIOD_2_RXN_m
set(['m'])
Glyma.19G009100
set(['n'])
---------
1_PERIOD_2_PERIOD_1_PERIOD_2_RXN_m
set(['m'])
Glyma.13G168700
set(['n'])
---------
1_PERIOD_2_PERIOD_1_PERIOD_2_RXN_m
set(['m'])
Glyma.19G009

---------
SERINE_O_ACETTRAN_RXN_c
set(['c'])
Glyma.02G042000
set(['m'])
---------
GPH_RXN_p
set(['p'])
Glyma.09G247900
set(['p'])
---------
GPH_RXN_p
set(['p'])
Glyma.09G015500
set(['c'])
---------
GPH_RXN_p
set(['p'])
Glyma.18G244900
set(['p'])
---------
GPH_RXN_p
set(['p'])
Glyma.15G121300
set(['c'])
---------
SUCROSE_PHOSPHATE_SYNTHASE_RXN_c
set(['c'])
Glyma.13G161600
set(['n'])
---------
SUCROSE_PHOSPHATE_SYNTHASE_RXN_c
set(['c'])
Glyma.18G108100
set(['p', 'c', 'n'])
---------
SUCROSE_PHOSPHATE_SYNTHASE_RXN_c
set(['c'])
Glyma.06G323700
set(['p', 'c', 'n'])
---------
SUCROSE_PHOSPHATE_SYNTHASE_RXN_c
set(['c'])
Glyma.04G110200
set(['p'])
---------
SUCROSE_PHOSPHATE_SYNTHASE_RXN_c
set(['c'])
Glyma.14G029100
set(['p', 'c', 'n'])
---------
SUCROSE_PHOSPHATE_SYNTHASE_RXN_c
set(['c'])
Glyma.17G109700
set(['r'])
---------
SUCROSE_PHOSPHATE_SYNTHASE_RXN_c
set(['c'])
Glyma.08G308600
set(['p', 'c', 'n'])
---------
SERINE_GLYOXYLATE_AMINOTRANSFERASE_RXN_x
set(['x'])
Glyma.10G122900
set(['x'])


---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.04G173400
set(['c'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.09G153900
set(['r'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.16G204600
set(['r', 'm'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.15G207600
set(['c'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.04G157000
set(['c'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.02G304200
set(['n'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.03G190500
set(['n'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.19G190900
set(['n'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.19G068500
set(['c'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.14G009600
set(['n'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.06G208200
set(['p'])
---------
2PGADEHYDRAT_RXN_p
set(['p'])
Glyma.15G235300
set(['m'])
---------
GDPKIN_RXN_c
set(['c'])
Glyma.05G045200
set(['p'])
---------
GDPKIN_RXN_c
set(['c'])
Glyma.17G127400
set(['p'])
---------
RXN_9659_p
set(['p'])
Glyma.08G345900
set(['p', 'r', 'n'])


In [27]:
removeGeneDict

{'10_FORMYL_THF_pc': [],
 '1TRANSKETO_RXN_p': [<Gene Glyma.01G120200 at 0x7f0af22d2690>,
  <Gene Glyma.03G027500 at 0x7f0af22d2610>],
 '1_ACYLGLYCEROL_3_P_ACYLTRANSFER_RXN_p': [],
 '1_PERIOD_10_PERIOD_2_PERIOD_2_RXN_mc': [<Gene Glyma.05G092000 at 0x7f0af22e5e50>,
  <Gene Glyma.07G122200 at 0x7f0af22e5d10>,
  <Gene Glyma.15G114600 at 0x7f0af22e5dd0>],
 '1_PERIOD_10_PERIOD_2_PERIOD_2_RXN_mi': [<Gene Glyma.05G092000 at 0x7f0af22e5e50>,
  <Gene Glyma.07G122200 at 0x7f0af22e5d10>,
  <Gene Glyma.15G114600 at 0x7f0af22e5dd0>],
 '1_PERIOD_18_PERIOD_1_PERIOD_2_RXN_p': [],
 '1_PERIOD_1_PERIOD_1_PERIOD_178_RXN_x': [],
 '1_PERIOD_1_PERIOD_1_PERIOD_255_RXN_c': [],
 '1_PERIOD_1_PERIOD_1_PERIOD_39_RXN_m': [<Gene Glyma.10G130600 at 0x7f0af230be50>,
  <Gene Glyma.05G091000 at 0x7f0af230bf10>,
  <Gene Glyma.20G081400 at 0x7f0af230bf50>],
 '1_PERIOD_2_PERIOD_1_PERIOD_13_RXN_p': [<Gene Glyma.16G044900 at 0x7f0af220f690>,
  <Gene Glyma.06G015900 at 0x7f0af220f6d0>,
  <Gene Glyma.19G106800 at 0x7f0af220f550

In [28]:
for rxn in removeGeneDict.keys():
    print rxn
    rxn = model2.reactions.get_by_id(rxn)
    tmp = rxn.gene_reaction_rule
    print tmp
    for gene in removeGeneDict[rxn.id]:
        tmp = tmp.replace("("+gene.id+")","").replace("( or ","(").replace("or  or","or").replace(" or )",")").replace("( )","")
    print tmp
    rxn.gene_reaction_rule = tmp
model2.genes._generate_index()

INORGPYROPHOSPHAT_RXN_c
((Glyma.04G028800) or (Glyma.17G108500) or (Glyma.03G262000) or (Glyma.07G011700) or (Glyma.10G147500) or (Glyma.15G023100) or (Glyma.07G028500) or (Glyma.07G001500) or (Glyma.03G172700) or (Glyma.08G194900) or (Glyma.19G173600) or (Glyma.08G225500) or (Glyma.08G214300) or (Glyma.13G060200) or (Glyma.13G351600) or (Glyma.U010400) or (Glyma.15G061300) or (Glyma.18G110900) or (Glyma.08G029600) or (Glyma.19G026600) or (Glyma.07G048300) or (Glyma.02G157000) or (Glyma.07G011900) or (Glyma.10G044700) or (Glyma.18G135600) or (Glyma.19G261100) or (Glyma.07G011800) or (Glyma.01G172400) or (Glyma.16G017200) or (Glyma.11G070800) or (Glyma.13G351700) or (Glyma.20G098300) or (Glyma.13G253600) or (Glyma.02G209900) or (Glyma.05G042100) or (Glyma.12G002600) or (Glyma.11G141400) or (Glyma.13G132400) or (Glyma.08G195100) or (Glyma.15G023000) or (Glyma.13G162800) or (Glyma.08G195000))
((Glyma.04G028800) or (Glyma.03G262000) or (Glyma.15G023100) or (Glyma.03G172700) or (Glyma.08G19

cobra/core/reaction.py:446 UserWarning: malformed gene_reaction_rule '()' for <Reaction DIAMINOPIMEPIM_RXN_p at 0x7f0af21f3790>
cobra/core/reaction.py:446 UserWarning: malformed gene_reaction_rule '()' for <Reaction IGPSYN_RXN_p at 0x7f0af21f3190>
cobra/core/reaction.py:446 UserWarning: malformed gene_reaction_rule '()' for <Reaction CONIFERIN_BETA_GLUCOSIDASE_RXN_c at 0x7f0af2114c50>
cobra/core/reaction.py:446 UserWarning: malformed gene_reaction_rule '()' for <Reaction RXN0_5260_m at 0x7f0af2114210>
cobra/core/reaction.py:446 UserWarning: malformed gene_reaction_rule '()' for <Reaction GLUCOKIN_RXN_c at 0x7f0af212b790>
cobra/core/reaction.py:446 UserWarning: malformed gene_reaction_rule '()' for <Reaction SULFITE_REDUCTASE_FERREDOXIN_RXN_p at 0x7f0af20f0ad0>
cobra/core/reaction.py:446 UserWarning: malformed gene_reaction_rule '()' for <Reaction GLUCOKIN_RXN_p at 0x7f0af212b9d0>
cobra/core/reaction.py:446 UserWarning: malformed gene_reaction_rule '()' for <Reaction 2_PERIOD_7_PERIOD_7

In [29]:
i=0
for rxn  in model.reactions:
    if len(rxn.genes)>0:
        i = i+1
print i

401


In [30]:
i=0
for gene in model.genes:
    if len(gene.reactions)==0:
        continue
    i=i+1
print i

2098


In [31]:
i=0
for rxn  in model2.reactions:
    if len(rxn.genes)>0:
        i = i+1
print i

325


In [32]:
model2.genes._generate_index()
i=0
for gene in model2.genes:
    if len(gene.reactions)==0:
        continue
    i=i+1
print i

1082


In [33]:
io.write_sbml_model(model2,"/home/sanu/Documents/Scripts/git/tissue-specific-FBA-models/Data/Soy_core_model_GA.sbml")

ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.sbml:LibSBML error code -3: The requested action could not be performed. This can occur in a variety of contexts, such as passing a null object as a parameter in a situation where it does not make sense to permit a null object.
ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.sbml:LibSBML error code -3: The requested action could not be performed. This can occur in a variety of contexts, such as passing a null object as a parameter in a situation where it does not make sense to permit a null object.
ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.sbml:LibSBML error code -3: The requested action could not be performed. This can occur in a variety of contexts, such as passing a null object as a parameter in a situation where it does not make sense to permit a null object.
ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.

ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.sbml:LibSBML error code -3: The requested action could not be performed. This can occur in a variety of contexts, such as passing a null object as a parameter in a situation where it does not make sense to permit a null object.
ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.sbml:LibSBML error code -3: The requested action could not be performed. This can occur in a variety of contexts, such as passing a null object as a parameter in a situation where it does not make sense to permit a null object.
ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.sbml:LibSBML error code -3: The requested action could not be performed. This can occur in a variety of contexts, such as passing a null object as a parameter in a situation where it does not make sense to permit a null object.
ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.

ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.sbml:LibSBML error code -3: The requested action could not be performed. This can occur in a variety of contexts, such as passing a null object as a parameter in a situation where it does not make sense to permit a null object.
ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.sbml:LibSBML error code -3: The requested action could not be performed. This can occur in a variety of contexts, such as passing a null object as a parameter in a situation where it does not make sense to permit a null object.
ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.sbml:LibSBML error code -3: The requested action could not be performed. This can occur in a variety of contexts, such as passing a null object as a parameter in a situation where it does not make sense to permit a null object.
ERROR:cobra.io.sbml:Error encountered trying to <set gpr: ( )>.
ERROR:cobra.io.

In [38]:
model.reactions.get_by_id("2PGADEHYDRAT_RXN_c").genes

frozenset({<Gene Glyma.04G157000 at 0x7f0b17e01a90>,
           <Gene Glyma.04G173400 at 0x7f0b17e01e90>,
           <Gene Glyma.04G144300 at 0x7f0b17e01f50>,
           <Gene Glyma.19G068500 at 0x7f0b17e01f90>,
           <Gene Glyma.03G190500 at 0x7f0b17e05050>,
           <Gene Glyma.19G190900 at 0x7f0b17e05090>,
           <Gene Glyma.15G235300 at 0x7f0b17e050d0>,
           <Gene Glyma.06G208200 at 0x7f0b17e05110>,
           <Gene Glyma.16G204600 at 0x7f0b17e05150>,
           <Gene Glyma.09G153900 at 0x7f0b17e05190>,
           <Gene Glyma.15G207600 at 0x7f0b17e051d0>,
           <Gene Glyma.14G009600 at 0x7f0b17e7b110>,
           <Gene Glyma.02G304200 at 0x7f0b17e7b8d0>})